# Are Our Street Trees Safe?

Question 3: In recent years, we've been having more severe weather conditions. Are our street trees safe? How old are they? Where are tall trees located?

```{note}
Please hit "Click to show" to see Python codes.
```

In [1]:
import pandas as pd
import numpy as np
import altair as alt
from datetime import date
alt.data_transformers.disable_max_rows()
pd.options.mode.chained_assignment = None #suppress warning

In [2]:
# use small dataset (5000 rows)
url = 'https://raw.githubusercontent.com/UBC-MDS/data_viz_wrangled/main/data/Trees_data_sets/small_vancouver_trees.csv'

# make sure date_planted has a data type "datetime"
data = pd.read_csv(url, parse_dates=[5])

In [3]:
# FUNCTIONS
# get height range description from height_range_id
def get_height_range_desc(height_range):
    if height_range == 0:
        return '0-10 ft'
    elif height_range == 1:
        return '10-20 ft'
    elif height_range == 2:
        return '20-30 ft'
    elif height_range == 3:
        return '30-40 ft'
    elif height_range == 4:
        return '40-50 ft'
    elif height_range == 5:
        return '50-60 ft'
    elif height_range == 6:
        return '60-70 ft'
    elif height_range == 7:
        return '70-80 ft'
    elif height_range == 8:
        return '80-90 ft'
    elif height_range == 9:
        return '90-100 ft'
    elif height_range == 10:
        return '100+ ft'
    else:
        return ''

In [4]:
# remove columns that will not be used for visualization
df = data.drop(columns=['Unnamed: 0','std_street','assigned','street_side_name','civic_number','plant_area','curb','tree_id','cultivar_name','root_barrier'], axis=1)

# rename columns
df.rename(columns={
    'on_street':'street',
    'species_name':'species',
    'neighbourhood_name':'neighbourhood',
    'genus_name':'genus',
    'height_range_id':'height_range'
}, inplace=True)

# convert data type
df['diameter'] = df['diameter'].astype(int)
df['on_street_block'] = df['on_street_block'].astype(str)

# add calculated fields from other columns
df['allergen'] = np.where(df['genus'].isin(['ALNUS','FAGUS','BETULA','TYPHA','CASTANEA','ULMUS','CORYLUS','TSUGA','LARIX','ACER','QUERCUS','POPULUS']), True, False)
df['year'] = pd.DatetimeIndex(df['date_planted']).year
df['year'].fillna(0, inplace=True)
df['year'] = df['year'].astype(int)
df['height_range_desc'] = df['height_range'].apply(get_height_range_desc)
df['st_block'] = df['on_street_block'] + ' ' + df['street']


In [5]:
height_plot2 = alt.Chart(df).mark_bar().encode(
    alt.X('height_range_desc', title='Height Range'),
    alt.Y('count():Q', title='Number of trees planted')
).properties(height=150, width=300, title='Height')

diameter_plot2 = height_plot2.mark_bar(color='orange').encode(
    alt.X('diameter:Q', title='Diameter (inches)')
).properties(title='Diameter')

height_plot2 | diameter_plot2

alt.HConcatChart(...)

<u>Formula: average height of planted trees</u>


$$
H
=
\frac{1}{n} 
(h_{1} + h_{2} + \cdots + h_{n})
$$

Most trees are between 10 and 70 feet tall.

The majority of trees are not so wide. It looks like many trees are only a few inches in diameter.

In [6]:
# Vancouver map
url_geojson = 'https://raw.githubusercontent.com/UBC-MDS/exploratory-data-viz/main/data/local-area-boundary.geojson'
data_geojson_remote = alt.Data(url=url_geojson, format=alt.DataFormat(property='features',type='json'))

vancouver_map = alt.Chart(data_geojson_remote).mark_geoshape(
    color = 'gray', opacity= 0.5, stroke='white').encode(
).project(type='identity', reflectY=True)

In [7]:
tree_map = alt.Chart(df).mark_circle(size=15).encode(
    longitude='longitude',
    latitude='latitude',
    tooltip=[alt.Tooltip('neighbourhood:N', title='Neighbourhood: '),
             alt.Tooltip('st_block:N', title='Street Block: '),
             alt.Tooltip('height_range_desc:O', title='Height Range: '),
             alt.Tooltip('diameter:Q', title='Diameter (inches)'),
             alt.Tooltip('age:O', title='Age (years): ')
            ],
    color=alt.Color('height_range_desc:O', title='Height Ranges', scale=alt.Scale(scheme='goldgreen'))
).project(type='identity', reflectY=True)

# create legend widget
select_height = alt.selection_multi(fields=['height_range_desc'], bind='legend')

tree_map = tree_map.encode(
    opacity=alt.condition(select_height, alt.value(1.0), alt.value(0.1)),
    size=alt.condition(select_height, alt.value(50), alt.value(15))  
).add_selection(select_height)

map_1 = (vancouver_map + tree_map
).properties(width=800, height=400, title=alt.TitleParams('Map 1 - Street trees by height range', 
                                                          subtitle='Click on the legend to highlight height range(s)', 
                                                          subtitleColor='purple',
                                                          anchor='middle'
                                                         )
            )
map_1.configure_view(stroke=None)

alt.LayerChart(...)

Click on the legend to select height range(s) and find where tall trees are located on the map. Hover over a circle on the map to see more information about the tree.
NOTE: Age information does not apply to all trees. More than half of the data is missing the planted year information. Trees taller than 80 feet do not have age information at all.